In [1]:
%load_ext autoreload
%autoreload 2


from numpy import random
from sklearn.metrics import average_precision_score
from sklearn.metrics import roc_auc_score
# noinspection PyUnresolvedReferences
from hcve_lib.tracking import load_run_results
from hcve_lib.utils import notebook_init, run_parallel
from hcve_lib.metrics import precision_recall_curve_with_confusion
from hcve_lib.evaluation_functions import map_inverse_weight

notebook_init()


from notebooks.deps.binary_predictive_performance import run_roc_analysis, get_pr_analysis
from notebooks.deps.binary_predictive_performance import get_pr_analysis, get_pr_analysis_ci, plot_pr_ci

from mlflow import set_tracking_uri
from notebooks.deps.config import TIME_POINT_PREDICTION
from deps.common import get_data_cached

from sklearn.metrics import roc_curve
from pandas import DataFrame
from plotly.graph_objs import Figure

from deps.constants import RANDOM_STATE
from hcve_lib.evaluation_functions import average_group_scores, merge_standardize_prediction, merge_predictions, \
    compute_metrics_prediction
from hcve_lib.metrics import BootstrappedMetric
from hcve_lib.tracking import load_group_results
from hcve_lib.visualisation import setup_plotly_style
from hcve_lib.functional import t
import numpy as np
from hcve_lib.metrics import statistic_from_bootstrap
from hcve_lib.functional import reject_none
from plotly import express as px
from hcve_lib.utils import transpose_list
from notebooks.deps.binary_predictive_performance import run_pr_analysis_ci

from config import GROUPS_LCO, GROUPS_10_fold
from hcve_lib.metrics import BinaryMetricFromScore
from hcve_lib.data import binarize_event

set_tracking_uri('http://localhost:5000')

<frozen importlib._bootstrap>:228: RuntimeWarning: sklearn.tree._splitter.Splitter size changed, may indicate binary incompatibility. Expected 360 from C header, got 1160 from PyObject


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [2]:
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)  

In [3]:
data, metadata, X, y = get_data_cached()


[Memory]0.1s, 0.0min    : Loading get_data...
____________________________________________get_data cache loaded - 0.0s, 0.0min


In [4]:
from hcve_lib.functional import dict_subset

GROUPS = dict_subset(['gb', 'coxnet', 'stacking', 'pcp_hf'], GROUPS_LCO)

In [65]:
TIME_POINT_PREDICTION = 10*365
ITERATIONS = 50

In [6]:
from hcve_lib.metrics import StratifiedMetric
from deps.data import get_30_to_80

pr_metrics_unweighted = (
    StratifiedMetric(
        BinaryMetricFromScore(precision_recall_curve_with_confusion, time=TIME_POINT_PREDICTION, sample_weight=None),
        splits={'30_to_80': list(get_30_to_80(X).index)}
    ),
#     BinaryMetricFromScore(average_precision_score, time=TIME_POINT_PREDICTION, sample_weight=None),
)

In [7]:
y_binarized_10_years = binarize_event(TIME_POINT_PREDICTION, y['data'], drop_censored=False)

print('Before')
print(y['data']['label'].value_counts().to_dict())
print('↓')
print(f'Binarization {TIME_POINT_PREDICTION/365} years (NA removed)')
print((y_binarized_10_years.value_counts() - y['data']['label'].value_counts()).to_dict())
print('↓')
print(y_binarized_10_years.value_counts(dropna=True).to_dict())


Before
{0.0: 29286, 1.0: 1068}
↓
Binarization 10.0 years (NA removed)
{0.0: -27294, 1.0: -177}
↓
{0.0: 1992, 1.0: 891}


/home/sitnarf/projects/hcve_lib/hcve_lib/data.py:247: FutureWarning:

The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.



In [8]:
y_binarized_5_years = binarize_event(5*365, y['data'], drop_censored=False)


/home/sitnarf/projects/hcve_lib/hcve_lib/data.py:247: FutureWarning:

The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.



In [9]:
inverse_weight_cohorts = map_inverse_weight(data['STUDY'].loc[y_binarized_10_years.index])

pr_metrics_weighted_cohorts = [
    BinaryMetricFromScore(precision_recall_curve_with_confusion, time=TIME_POINT_PREDICTION, sample_weight=inverse_weight_cohorts),
    BinaryMetricFromScore(average_precision_score, time=TIME_POINT_PREDICTION, sample_weight=inverse_weight_cohorts),
]

In [10]:
inverse_incident_weight = map_inverse_weight(y_binarized_10_years, proportions={1:0.03, 0: 0.97})

pr_metrics_incidence_weighted = [
    BinaryMetricFromScore(precision_recall_curve_with_confusion, time=TIME_POINT_PREDICTION, sample_weight=inverse_incident_weight),
    BinaryMetricFromScore(average_precision_score, time=TIME_POINT_PREDICTION, sample_weight=inverse_incident_weight),
]

In [11]:

combined_weight = (inverse_weight_cohorts*inverse_incident_weight).dropna()

pr_metrics_incidence_cohort_weighted = [
    BinaryMetricFromScore(precision_recall_curve_with_confusion, time=TIME_POINT_PREDICTION, sample_weight=combined_weight),
    BinaryMetricFromScore(average_precision_score, time=TIME_POINT_PREDICTION, sample_weight=combined_weight),
]

In [12]:
from toolz import valmap 

merged_prediction = valmap(
    lambda group_id: merge_predictions(average_group_scores(load_group_results(group_id))),
    GROUPS,
)


In [13]:
import pandas

def get_fu_df():
    fu_df = pandas.concat(
        [
            y['data'],
            data,
        ],
        axis=1,
        join='inner',
    )
    fu_df['tte'] /= 365
    fu_df['jitter'] = [random.normal() for _ in range(len(fu_df))]
    return fu_df

fu_df = get_fu_df()

In [14]:
fu_df['y_binarized_5_years'] = y_binarized_5_years
fu_df['y_binarized_10_years'] = y_binarized_10_years
fu_df['gb'] = merged_prediction['gb']['y_score']
fu_df['coxnet'] = merged_prediction['coxnet']['y_score']
fu_df['pcp_hf'] = merged_prediction['pcp_hf']['y_score']
fu_df['stacking'] = merged_prediction['stacking']['y_score']

In [15]:
y_sampled = y['data'].sample(5000)
data_ = data.loc[y_sampled.index]

In [16]:
from numpy import random

fig = px.scatter(fu_df[fu_df['label']==1], x='tte', y='jitter', color='STUDY', opacity=0.8)
setup_plotly_style(fig)
fig.show()

In [17]:
from numpy import random

fig = px.scatter(fu_df, x='tte', y='jitter', color='STUDY', opacity=0.8)
setup_plotly_style(fig)
fig.show()

## Cases and controls for 5 years

In [18]:
from numpy import random

fig = px.scatter(fu_df[(~fu_df['y_binarized_5_years'].isna())], x='tte', y='jitter', color='STUDY', opacity=0.5)
setup_plotly_style(fig)
fig.add_vline(x=5, line_width=3, line_dash="dash", opacity=0.7)
fig.show()

## Cases and controls for 10 years

binarization removes a lot of cluttered controls (< 5 years). actually good, we don't want most of "metric" be computed on "relatively close" time scale.

In [19]:
from numpy import random

fig = px.scatter(fu_df[(~fu_df['y_binarized_10_years'].isna())], x='tte', y='jitter', color='STUDY', opacity=0.5)
setup_plotly_style(fig)
fig.add_vline(x=10, line_width=3, line_dash="dash", opacity=0.7)
fig.show()

## Scores

In [20]:
from numpy import random

fig = px.scatter(
    fu_df[(~fu_df['y_binarized_10_years'].isna())],
    title='stacking',
    x='tte',
    y='jitter',
    color='stacking',
    opacity=0.5,
    range_color=[0,100],
)
setup_plotly_style(fig)
fig.add_vline(x=10, line_width=3, line_dash="dash", opacity=0.7)
fig.show()

In [21]:
from numpy import random

fig = px.scatter(
    fu_df[(~fu_df['y_binarized_10_years'].isna())],
    title='pcp_hf',
    x='tte',
    y='jitter',
    color='pcp_hf',
    opacity=0.5,
    range_color=[5,40],

)
setup_plotly_style(fig)
fig.add_vline(x=10, line_width=3, line_dash="dash", opacity=0.7)
fig.show()

In [22]:
from numpy import random

fig = px.scatter(
    fu_df[(~fu_df['y_binarized_10_years'].isna())],
    title='gb',
    x='tte',
    y='jitter',
    color='gb',
    opacity=0.5,
)
setup_plotly_style(fig)
fig.add_vline(x=10, line_width=3, line_dash="dash", opacity=0.7)
fig.show()

In [23]:
from numpy import random

fig = px.scatter(
    fu_df[(~fu_df['y_binarized_10_years'].isna())],
    title='coxnet',
    x='tte',
    y='jitter',
    color='coxnet',
    opacity=0.5,
)
setup_plotly_style(fig)
fig.add_vline(x=10, line_width=3, line_dash="dash", opacity=0.7)
fig.show()

In [24]:
fu_df[['stacking', 'gb', 'coxnet', 'pcp_hf']].corr()

stacking        gb    coxnet    pcp_hf
stacking  1.000000  0.666799  0.275756  0.425112
gb        0.666799  1.000000  0.679392  0.414919
coxnet    0.275756  0.679392  1.000000  0.511820
pcp_hf    0.425112  0.414919  0.511820  1.000000

In [36]:
from toolz import valmap 
from numpy.random import seed
from numpy.random import randint
from scipy.stats import ks_2samp

merged_prediction = valmap(
    lambda group_id: merge_predictions(average_group_scores(load_group_results(group_id))),
    GROUPS,
)


In [66]:
pr = get_pr_analysis(
    GROUPS,
    y,
    metrics=[
        BinaryMetricFromScore(
            average_precision_score,
            time=TIME_POINT_PREDICTION,
            sample_weight=inverse_weight_cohorts)
    ], 
    standardize=False,
    iterations=ITERATIONS
)

[Memory]3588.3s, 59.8min: Loading load_group_results...
_________________________________load_group_results cache loaded - 38.7s, 0.6min
[Memory]3630.9s, 60.5min: Loading load_group_results...
_________________________________load_group_results cache loaded - 10.4s, 0.2min
[Memory]3644.4s, 60.7min: Loading load_group_results...
_________________________________load_group_results cache loaded - 37.9s, 0.6min
[Memory]3685.7s, 61.4min: Loading load_group_results...
__________________________________load_group_results cache loaded - 0.1s, 0.0min


In [73]:
from pandas import read_csv
from scipy.stats import normaltest
from matplotlib import pyplot

for name in ['coxnet', 'gb', 'pcp_hf', 'stacking']:

    value, p = normaltest(pr[name]['average_precision_score_3650'])
    print(name, f'p={p:.3f}')
    if p >= 0.05:
        print('It is likely that result1 is normal')
    else:
        print('It is unlikely that result1 is normal')

coxnet p=0.040
It is unlikely that result1 is normal
gb p=0.779
It is likely that result1 is normal
pcp_hf p=0.113
It is likely that result1 is normal
stacking p=0.860
It is likely that result1 is normal


In [91]:
from itertools import combinations
from scipy.stats import ttest_ind
from pandas import Series

scores_df = {method: pr[method]['average_precision_score_3650'] for method in ['coxnet', 'gb', 'pcp_hf', 'stacking']}

for (name1, s1), (name2, s2) in combinations(scores_df.items(), 2):
    print(name1, name2)
    print(', '.join([f'{v:.2f}' for v in Series(s1).sample(10)]))
    print(', '.join([f'{v:.2f}' for v in Series(s2).sample(10)]))
    
    ks = ks_2samp(s1, s2)
    print(f"KS: {ks.statistic:.4f} (p-value: {ks.pvalue:.1e})")
    
    value, pvalue = ttest_ind(s1, s2)
    print(f"t-test: p-value: {pvalue:.1e}")
    
    print()
    

coxnet gb
0.48, 0.46, 0.48, 0.47, 0.45, 0.49, 0.49, 0.47, 0.42, 0.44
0.52, 0.50, 0.51, 0.49, 0.49, 0.48, 0.49, 0.53, 0.46, 0.48
KS: 0.5600 (p-value: 1.5e-07)
t-test: p-value: 1.9e-11

coxnet pcp_hf
0.43, 0.48, 0.47, 0.49, 0.41, 0.46, 0.47, 0.47, 0.44, 0.44
0.48, 0.45, 0.47, 0.48, 0.47, 0.45, 0.42, 0.45, 0.45, 0.44
KS: 0.1600 (p-value: 5.5e-01)
t-test: p-value: 6.8e-01

coxnet stacking
0.49, 0.44, 0.49, 0.49, 0.45, 0.44, 0.45, 0.47, 0.47, 0.45
0.67, 0.61, 0.64, 0.65, 0.66, 0.68, 0.68, 0.68, 0.66, 0.64
KS: 1.0000 (p-value: 2.0e-29)
t-test: p-value: 3.3e-68

gb pcp_hf
0.50, 0.48, 0.49, 0.49, 0.52, 0.47, 0.50, 0.48, 0.46, 0.51
0.50, 0.47, 0.48, 0.43, 0.46, 0.47, 0.43, 0.45, 0.47, 0.53
KS: 0.6400 (p-value: 6.1e-10)
t-test: p-value: 1.9e-13

gb stacking
0.47, 0.51, 0.49, 0.49, 0.52, 0.51, 0.49, 0.53, 0.50, 0.50
0.68, 0.65, 0.68, 0.67, 0.64, 0.63, 0.66, 0.66, 0.62, 0.65
KS: 1.0000 (p-value: 2.0e-29)
t-test: p-value: 8.2e-65

pcp_hf stacking
0.45, 0.48, 0.48, 0.45, 0.48, 0.47, 0.46, 0.46, 0.47

In [ ]:
y_binarized_10_years = binarize_event(TIME_POINT_PREDICTION, y['data'], drop_censored=False)

print('Before')
print(y['data']['label'].value_counts().to_dict())
print('↓')
print(f'Binarization {TIME_POINT_PREDICTION/365} years (NA removed)')
print((y_binarized.value_counts() - y['data']['label'].value_counts()).to_dict())
print('↓')
print(y_binarized.value_counts(dropna=True).to_dict())


In [30]:
values1dd

array([55, 58, 59, 55, 50, 50, 51, 57, 56, 59, 52, 54, 55, 52, 54, 52, 54,
       57, 57, 59, 51, 57, 50, 56, 59, 59, 57, 56, 59, 51, 50, 51, 58, 58,
       53, 59, 58, 57, 53, 56, 55, 51, 59, 53, 54, 58, 51, 54, 50, 53, 59,
       52, 50, 54, 59, 52, 57, 57, 59, 58, 56, 59, 53, 57, 57, 54, 55, 59,
       53, 56, 58, 50, 52, 57, 57, 59, 57, 53, 50, 58, 57, 57, 51, 51, 53,
       50, 58, 56, 54, 55, 56, 52, 55, 57, 58, 54, 54, 57, 57, 54])

In [ ]:
y_binarized_5_years = binarize_event(5*365, y['data'], drop_censored=False)


## Interpreting stacking metamodel

In [ ]:
from toolz import valmap 

merged_prediction = valmap(
    lambda group_id: merge_predictions(average_group_scores(load_group_results(group_id))),
    GROUPS,
)

In [ ]:
group_stacking = load_group_results(GROUPS['stacking'], load_models=True)

In [ ]:
setattr(tree, 'criterion', 'log_loss')

In [ ]:
for cohort_name, prediction in group_stacking[0].items():
    clf = prediction['model'].fit_best_model[-1].final_estimator_
    base_estimators = prediction['model'].fit_best_model[-1].base_estimators
    n_nodes = clf.tree_.node_count
    children_left = clf.tree_.children_left
    children_right = clf.tree_.children_right
    feature = clf.tree_.feature
    threshold = clf.tree_.threshold

    node_depth = np.zeros(shape=n_nodes, dtype=np.int64)
    is_leaves = np.zeros(shape=n_nodes, dtype=bool)
    stack = [(0, 0)]  # start with the root node id (0) and its depth (0)
    while len(stack) > 0:
        # `pop` ensures each node is only visited once
        node_id, depth = stack.pop()
        node_depth[node_id] = depth

        # If the left and right child of a node is not the same we have a split
        # node
        is_split_node = children_left[node_id] != children_right[node_id]
        # If a split node, append left and right children and depth to `stack`
        # so we can loop through them
        if is_split_node:
            stack.append((children_left[node_id], depth + 1))
            stack.append((children_right[node_id], depth + 1))
        else:
            is_leaves[node_id] = True

    print(
        "The binary tree structure has {n} nodes and has "
        "the following tree structure:\n".format(n=n_nodes)
    )
    for i in range(n_nodes):
        if is_leaves[i]:
            print(
                "{space}{node}: leaf".format(
                    space=node_depth[i] * " ", node=i
                )
            )
        else:
            print(
                "{space}{node}: {left} if {feature} <= {threshold:.2f} else {right} ".format(
                    space=node_depth[i] * " ",
                    node=i,
                    left=children_left[i],
                    feature=base_estimators[feature[i]][0],
                    threshold=threshold[i],
                    right=children_right[i],
                )
            )

In [35]:
dcapy.__dict__

{'__name__': 'dcapy',
 '__doc__': None,
 '__package__': 'dcapy',
 '__loader__': <_frozen_importlib_external._NamespaceLoader at 0x7f2ce2e8a070>,
 '__spec__': ModuleSpec(name='dcapy', loader=<_frozen_importlib_external._NamespaceLoader object at 0x7f2ce2e8a070>, submodule_search_locations=_NamespacePath(['/home/sitnarf/projects/homage-fl/dcapy'])),
 '__file__': None,
 '__path__': _NamespacePath(['/home/sitnarf/projects/homage-fl/dcapy'])}